In [1]:
%pip install -q dotenv
%pip install -q kagglehub
%pip install -q ipywidgets
%pip install -q tensorflow
%pip install -q tensorflow_datasets
%pip install -q tensorboardX
%pip install -q transformers
%pip install -q grain
%pip install -q git+https://github.com/jax-ml/jax
%pip install git+https://github.com/google/tunix
%pip install git+https://github.com/google/qwix
%pip uninstall -q flax -y
%pip install git+https://github.com/google/flax
%pip install -q huggingface_hub
%pip install -q datasets
%pip install -q 'numpy>2'

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Cloning https://github.com/google/tunix to /tmp/pip-req-build-vxvwmvmm
  Running command git clone --filter=blob:none --quiet https://github.com/google/tunix /tmp/pip-req-build-vxvwmvmm
  Resolved https://github.com/google/tunix to commit 974da5da91fb6959aa8d9111bd5a9334da81a2ea
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Cloning https://github.com/google/qwix to /tmp/pip-req-build-fpuk04vk
  Running command git clone --filter=blob:none --quiet https://github.com/google/qwix /tmp/pip-req-build-fpuk04vk
  Resolved https://github.com/google/qwix to commit 5a1b0df1a789d4198954d7f10609c0bd6d0bbfd4
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Cloning https://github.com/googl

In [2]:
import os

import kagglehub

try:
  from google.colab import userdata
  USE_COLAB = True

  %pip uninstall -q wandb -y  # wandb is glitchy with tunix in colab

  os.environ["HF_TOKEN"] = userdata.get("HF_TOKEN")
  os.environ["KAGGLE_USERNAME"] = userdata.get("KAGGLE_USERNAME")
  os.environ["KAGGLE_KEY"] = userdata.get("KAGGLE_KEY")
except:
  USE_COLAB = False

  from dotenv import load_dotenv
  load_dotenv()
  print("Using env vars to login")

  import nest_asyncio
  nest_asyncio.apply()
  print("nest_asyncio applied")

  # Only using wandb on TPU VM because it has strange bugs on Colab
  !pip install -q wandb
  import wandb
  # Check if WANDB_API_KEY is set before logging in
  if "WANDB_API_KEY" in os.environ and os.environ["WANDB_API_KEY"]:
      wandb.login(key=os.environ["WANDB_API_KEY"])
  else:
      print("WANDB_API_KEY not found. Skipping wandb login.")

if "KAGGLE_USERNAME" not in os.environ or "KAGGLE_KEY" not in os.environ:
  kagglehub.login()

if "HF_TOKEN" in os.environ and os.environ["HF_TOKEN"]:
    hf_token = os.environ["HF_TOKEN"]
    !hf auth login --token "$hf_token"
else:
    print("HF_TOKEN not found. Skipping Hugging Face login.")

Using env vars to login
nest_asyncio applied
WANDB_API_KEY not found. Skipping wandb login.


The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `hf`CLI if you want to set the git credential as well.
Token is valid (permission: fineGrained).
The token `hotblood` has been saved to /root/.cache/huggingface/stored_tokens
Your token has been saved to /root/.cache/huggingface/token
Login successful.
Note: Environment variable`HF_TOKEN` is set and is the current active token independently from the token you've just configured.


In [3]:
import functools
from pprint import pprint
import re
import sys

import csv
import json
import shutil

from flax import nnx
import grain
import humanize
from huggingface_hub import snapshot_download
import jax
import jax.numpy as jnp
import kagglehub
import numpy as np
import optax
from orbax import checkpoint as ocp
from pathlib import Path
import qwix
import tensorflow_datasets as tfds
from tqdm.auto import tqdm
from tunix.generate import sampler as sampler_lib
from tunix.generate import tokenizer_adapter as tokenizer_lib
from tunix.models.gemma3 import model as gemma_lib
from tunix.models.gemma3 import params_safetensors as params_safetensors_lib
from tunix.models.gemma3 import params as gemma_params
from tunix.rl import rl_cluster as rl_cluster_lib
from tunix.rl.grpo.grpo_learner import GRPOConfig, GRPOLearner
from tunix.rl.rollout import base_rollout
from tunix.sft import metrics_logger

/usr/local/lib/python3.12/dist-packages/jax/_src/cloud_tpu_init.py:93: UserWarning: Transparent hugepages are not enabled. TPU runtime startup and shutdown time should be significantly improved on TPU v5e and newer. If not already set, you may need to enable transparent hugepages in your VM image (sudo sh -c "echo always > /sys/kernel/mm/transparent_hugepage/enabled")
  warnings.warn(


In [4]:
# ====== Model ======
MODEL_ID = "google/gemma-3-1b-it"
GEMMA_TOKENIZER_PATH = "gs://gemma-data/tokenizers/tokenizer_gemma3.model"

# ====== Data ======
TRAIN_DATA_DIR = "./data/train"
TEST_DATA_DIR = "./data/test"
TRAIN_FRACTION = .9

# ====== LoRA ======
RANK = 64
ALPHA = 64.0

# ====== Sharding ======
# Adjust mesh based on your TPU memory and model size.
NUM_TPUS = len(jax.devices())
if NUM_TPUS == 8:
  MESH_COUNTS = (1, 4)
elif NUM_TPUS == 1:
  MESH_COUNTS = (1, 1)
else:
  raise ValueError(f"Unsupported number of TPUs: {NUM_TPUS}")

MESH = [
    MESH_COUNTS,
    ("fsdp", "tp"),
]

# ====== GRPO ======
# === Generation during GRPO training ===
MAX_PROMPT_LENGTH = 256
TOTAL_GENERATION_STEPS = 768
# Important to keep a high-ish temperature for varied, diverse responses during
# training.
TEMPERATURE = 0.9
TOP_P = 1.0
TOP_K = 50
# The number of times the policy generates multiple responses for a given prompt
# within a single training step. This corresponds to `G` in Algorithm 1 in the
# paper. The "group" in GRPO comes from here.
NUM_GENERATIONS = 2

# === other GRPO configs ===
# The number of iterations per batch (𝜇 in GRPO algo 1).
NUM_ITERATIONS = 1
# The coefficient for the KL divergence penalty (𝛽) in the GRPO loss function.
# Important to keep a high enough value for this, otherwise, the KL divergence
# can increase unchecked.
BETA = 0.08
# Epsilon value for clipping (𝜀 in GRPO loss in paper). Similar to PPO, for
# stable updates.
EPSILON = 0.2

# ====== Training ======
TRAIN_MICRO_BATCH_SIZE = 1
# Increase `NUM_BATCHES` and `MAX_STEPS` for better results.
NUM_BATCHES = 3738
# Keep `NUM_TEST_BATCHES` low so that evaluation runs quickly. It can be
# increased to a max. of 330 (if batch size is 4).
NUM_TEST_BATCHES = 64

EVAL_EVERY_N_STEPS = 64  # this doesn't matter if `TRAIN_FRACTION = 1.0`.
NUM_EPOCHS = 1  # can potentially train for more epochs

# Number of training steps.
MAX_STEPS = int(NUM_BATCHES * NUM_ITERATIONS * TRAIN_FRACTION * NUM_EPOCHS)

# === AdamW, warmup, cosine scheduler ===
LEARNING_RATE = 3e-6
B1 = 0.9
B2 = 0.99
WEIGHT_DECAY = 0.1
# == Cosine decay with warmup scheduler ==
# Linearly increase learning rate from 0. to 5e-6 in the first 10% training
# steps, and then gradually decrease the learning rate to 0 using cosine
# scheduler.
WARMUP_STEPS = 0.1 * MAX_STEPS
# == Grad clipping ==
# Grad clipping to prevent large gradients. Found this
# important to keep KL divergence in check.
MAX_GRAD_NORM = 0.1

# Checkpoint saving
INTERMEDIATE_CKPT_DIR = "/tmp/content/intermediate_ckpt/"
CKPT_DIR = "/tmp/content/ckpts/"
SAVE_INTERVAL_STEPS = 500
MAX_TO_KEEP = 4

# ====== Inference ======
GENERATION_CONFIGS = {
    # greedy search
    "greedy": {"temperature": None, "top_k": 1, "top_p": None},
    # some randomness
    "standard": {"temperature": 0.7, "top_k": 50, "top_p": 0.95},
    # liberal
    "liberal": {"temperature": 0.85, "top_k": 2000, "top_p": 1.0},
}

In [5]:
# ============================================================
# ScienceQA setup (tokens, template, dataset) + disable wandb
# ============================================================

import os
os.environ["WANDB_DISABLED"] = "true"
print("WANDB_DISABLED set to:", os.environ.get("WANDB_DISABLED"))

from datasets import load_dataset

# --- Special tokens for reasoning / answer ---
reasoning_start = "<reasoning>"
reasoning_end = "</reasoning>"
solution_start = "<answer>"
solution_end = "</answer>"

# ScienceQA HF dataset
SCIENCEQA_ID = "derek-thomas/ScienceQA"
CHOICE_LETTERS = ["A", "B", "C", "D", "E", "F"]

SYSTEM_PROMPT = f"""You are an expert science tutor.
First, think step by step about the science question and explain your reasoning
between {reasoning_start} and {reasoning_end}.
Then, give ONLY the letter (A, B, C, …) of the correct multiple-choice option
between {solution_start} and {solution_end}."""

TEMPLATE = """<start_of_turn>user
{system_prompt}

{question}<end_of_turn>
<start_of_turn>model
"""


def build_mc_question(example):
    """Format a ScienceQA example into a text block with context + choices."""
    q = example["question"]
    choices = example["choices"]

    lines = []

    # Optional context fields if present
    if example.get("hint"):
        if example["hint"]:
            lines.append(f"Hint: {example['hint']}")
    if example.get("lecture"):
        if example["lecture"]:
            lines.append(f"Lecture: {example['lecture']}")

    # Core question + choices
    lines.append(f"Question: {q}")
    lines.append("")
    lines.append("Choices:")
    for idx, choice in enumerate(choices):
        if idx >= len(CHOICE_LETTERS):
            break
        lines.append(f"{CHOICE_LETTERS[idx]}. {choice}")

    return "\n".join(lines)


def scienceqa_map_fn(ex):
    mc_text = build_mc_question(ex)
    prompt = TEMPLATE.format(system_prompt=SYSTEM_PROMPT, question=mc_text)

    # ScienceQA stores the correct option index in "answer"
    answer_idx = int(ex["answer"])
    answer_letter = CHOICE_LETTERS[answer_idx]

    return {
        "prompts": prompt,          # what GRPO will feed to the model
        "question": ex["question"], # raw question text (debugging / logging)
        "choices": ex["choices"],   # list of options
        "answer_letter": answer_letter,  # gold label (A/B/C/…)
    }


def get_scienceqa_dataset(split: str, num_batches: int):
    """
    Load ScienceQA split and convert into a Grain MapDataset that yields
    batched examples ready for GRPO.
    """
    raw = load_dataset(SCIENCEQA_ID, split=split)

    dataset = (
        grain.MapDataset.source(list(raw))
        .shuffle(seed=42)
        .map(scienceqa_map_fn)
        .batch(TRAIN_MICRO_BATCH_SIZE)
    )

    return dataset[:num_batches]


# --- Build train / val / test datasets (batched) ---

full_train = get_scienceqa_dataset("train", NUM_BATCHES)
test_dataset = get_scienceqa_dataset("validation", NUM_TEST_BATCHES)

if TRAIN_FRACTION == 1.0:
    train_dataset = full_train.repeat(NUM_EPOCHS)
    val_dataset = None
else:
    n_train_batches = int(len(full_train) * TRAIN_FRACTION)
    train_dataset = full_train[:n_train_batches].repeat(NUM_EPOCHS)
    val_dataset = full_train[n_train_batches:].repeat(NUM_EPOCHS)

print(
    "ScienceQA dataset sizes (batches):",
    len(train_dataset),
    len(val_dataset) if val_dataset is not None else 0,
    len(test_dataset),
)

# Peek at one batch to confirm structure
for ele in train_dataset[:1]:
    pprint(ele)
    break

WANDB_DISABLED set to: true
ScienceQA dataset sizes (batches): 3364 374 64
{'answer_letter': array(['B'], dtype='<U1'),
 'choices': [array(['ff'], dtype='<U2'), array(['light fur'], dtype='<U9')],
 'prompts': array(["<start_of_turn>user\nYou are an expert science tutor.\nFirst, think step by step about the science question and explain your reasoning\nbetween <reasoning> and </reasoning>.\nThen, give ONLY the letter (A, B, C, …) of the correct multiple-choice option\nbetween <answer> and </answer>.\n\nHint: In a group of rock pocket mice, some individuals have dark fur and others have light fur. In this group, the gene for the fur color trait has two alleles. The allele F is for dark fur, and the allele f is for light fur.\nNutmeg, a rock pocket mouse from this group, has light fur. Nutmeg has two alleles for light fur.\nLecture: All organisms have pieces of hereditary material called genes, which are passed from parents to offspring. Genes contain instructions for building the parts of

In [6]:
# ============================================================
# Reward functions for ScienceQA GRPO
# ============================================================

# --- Regex for exact format: <reasoning>...</reasoning><answer>...</answer> ---
match_format = re.compile(
    rf"^[\s]{{0,}}"
    rf"{reasoning_start}.+?{reasoning_end}.*?"
    rf"{solution_start}(.+?){solution_end}"
    rf"[\s]{{0,}}$",
    flags=re.MULTILINE | re.DOTALL,
)

example = f"{reasoning_start}Let me think!{reasoning_end}{solution_start}B{solution_end}"
print("Format example:", example)
print("Regex match:", bool(match_format.search(example)))


# 1) Exact format reward
def reward_format_exactly(prompts, completions, **kwargs):
    scores = []
    for response in completions:
        if response is None:
            scores.append(0.0)
            continue
        scores.append(3.0 if match_format.search(response) is not None else 0.0)
    return scores


# 2) Approximate format reward (soft shaping)
def reward_format_approximately(prompts, completions, **kwargs):
    scores = []

    for response in completions:
        if response is None:
            scores.append(0.0)
            continue

        s = 0.0
        s += 0.5 if response.count(reasoning_start) == 1 else -0.5
        s += 0.5 if response.find(reasoning_start) == 0 else -0.5
        s += 0.5 if response.count(reasoning_end) == 1 else -0.5
        s += 0.5 if response.count(solution_start) == 1 else -0.5
        s += 0.5 if response.count(solution_end) == 1 else -0.5

        scores.append(s)
    return scores


# 3) Multiple-choice correctness reward (A/B/C/…)
#    We look for a single letter A–F between <answer> and </answer>.
choice_letter_regex = re.compile(
    rf"{solution_start}\s*([A-Fa-f])\s*{solution_end}",
    flags=re.MULTILINE | re.DOTALL,
)

def reward_choice_correct(prompts, completions, answer_letter, **kwargs):
    """
    answer_letter: list of gold labels, e.g. ["B", "D", ...]
    """
    scores = []
    assert len(completions) == len(answer_letter), "Mismatched batch lengths"

    for response, gold in zip(completions, answer_letter):
        if response is None:
            scores.append(0.0)
            continue

        m = choice_letter_regex.search(response)
        if m is None:
            # No valid letter between tags → treat as no answer
            scores.append(0.0)
            continue

        guess = m.group(1).upper().strip()
        gold = str(gold).upper().strip()

        if guess == gold:
            scores.append(3.0)   # correct choice
        else:
            scores.append(-1.0)  # wrong choice
    return scores


# 4) Numbers reward stub (not used for ScienceQA, but kept for API symmetry)
def reward_numbers_stub(prompts, completions, **kwargs):
    return [0.0 for _ in completions]


# --- Tiny sanity check like before ---
_test_prompts = ["dummy"]
_test_completions = [
    f"{reasoning_start}Let me think!{reasoning_end}{solution_start}B{solution_end}",
    f"{reasoning_start}Another chain{reasoning_end}{solution_start}C{solution_end}",
    "No tags here at all",
]
_test_answers = ["B", "D", "A"]

print("\n=== Reward sanity check ===")
print("Exact format:", reward_format_exactly(_test_prompts, _test_completions))
print("Approx format:", reward_format_approximately(_test_prompts, _test_completions))
print("Choice correct:", reward_choice_correct(_test_prompts, _test_completions, _test_answers))
print("Numbers stub:", reward_numbers_stub(_test_prompts, _test_completions))


Format example: <reasoning>Let me think!</reasoning><answer>B</answer>
Regex match: True

=== Reward sanity check ===
Exact format: [3.0, 3.0, 0.0]
Approx format: [2.5, 2.5, -2.5]
Choice correct: [3.0, -1.0, 0.0]
Numbers stub: [0.0, 0.0, 0.0]


In [7]:
# ============================================================
# Load Gemma3-1B-it + apply LoRA policy for Science GRPO
# ============================================================

ignore_patterns = [
    "*.pth",  # Ignore PyTorch .pth weight files
]

print(f"Downloading {MODEL_ID} from Hugging Face...")
local_model_path = snapshot_download(
    repo_id=MODEL_ID,
    ignore_patterns=ignore_patterns,
)
print(f"Model successfully downloaded to: {local_model_path}")

# We'll also collect EOS tokens from the generation_config.json if present
EOS_TOKENS = []
generation_config_path = os.path.join(local_model_path, "generation_config.json")
if os.path.exists(generation_config_path):
    with open(generation_config_path, "r") as f:
        generation_configs = json.load(f)
    EOS_TOKENS = generation_configs.get("eos_token_id", [])
    print(f"Using EOS token IDs from generation_config: {EOS_TOKENS}")
else:
    print("No generation_config.json found; will fall back to tokenizer EOS.")


# ============================================================
# Build Gemma3 NNX model from safetensors checkpoint
# ============================================================

MODEL_CP_PATH = local_model_path

if "gemma-3-270m" in MODEL_ID:
    model_config = gemma_lib.ModelConfig.gemma3_270m()
elif "gemma-3-1b" in MODEL_ID:
    model_config = gemma_lib.ModelConfig.gemma3_1b()
else:
    raise ValueError(f"Unknown model id / config for MODEL_ID={MODEL_ID}")

print("Model config:", model_config)

# Create JAX mesh for sharding
mesh = jax.make_mesh(
    *MESH,
    axis_types=(jax.sharding.AxisType.Auto,) * len(MESH[0]),
)
print("Mesh devices:", mesh.devices)

with mesh:
    print("Creating Gemma3 model from safetensors...")
    gemma3 = params_safetensors_lib.create_model_from_safe_tensors(
        MODEL_CP_PATH,
        model_config,
        mesh,
    )
    nnx.display(gemma3)

print("Base Gemma3 model loaded ✅")


# ============================================================
# LoRA policy model
# ============================================================

def get_lora_model(base_model, mesh):
    lora_provider = qwix.LoraProvider(
        module_path=(
            ".*q_einsum|.*kv_einsum|.*gate_proj|.*down_proj|.*up_proj|"
            ".*attn_vec_einsum"
        ),
        rank=RANK,
        alpha=ALPHA,
    )

    model_input = base_model.get_model_input()
    lora_model = qwix.apply_lora_to_model(
        base_model, lora_provider, **model_input
    )

    with mesh:
        state = nnx.state(lora_model)
        pspecs = nnx.get_partition_spec(state)
        sharded_state = jax.lax.with_sharding_constraint(state, pspecs)
        nnx.update(lora_model, sharded_state)

    return lora_model

# Policy model = Gemma3 + LoRA adapters
lora_policy = get_lora_model(gemma3, mesh=mesh)
nnx.display(lora_policy)
print("LoRA policy model created ✅")


# ============================================================
# Tokenizer + EOS tokens
# ============================================================

tokenizer = tokenizer_lib.Tokenizer(tokenizer_path=GEMMA_TOKENIZER_PATH)

# Ensure tokenizer EOS is included in EOS_TOKENS
if tokenizer.eos_id() not in EOS_TOKENS:
    EOS_TOKENS.append(tokenizer.eos_id())

print(f"Final EOS_TOKENS used for sampling: {EOS_TOKENS}")


Fetching 10 files:   0%|          | 0/10 [00:00<?, ?it/s]

Model successfully downloaded to: /root/.cache/huggingface/hub/models--google--gemma-3-1b-it/snapshots/dcc83ea841ab6100d6b47a070329e1ba4cf78752
Using EOS token IDs from generation_config: [1, 106]
Model config: ModelConfig(num_layers=26, num_embed=262144, embed_dim=1152, hidden_dim=6912, num_heads=4, head_dim=256, num_kv_heads=1, sliding_window_size=512, local_base_frequency=10000, global_base_frequency=1000000, local_scale_factor=1.0, global_scale_factor=1.0, query_pre_attn_norm=<QueryPreAttentionNormalisation.BY_ONE_OVER_SQRT_HEAD_DIM: 1>, shd_config=ShardingConfig(emb_vd=('tp', 'fsdp'), q_weight_ndh=('tp', 'fsdp', None), kv_weight_cndh=(None, 'tp', 'fsdp', None), qkv_weight_cndh=(None, 'tp', 'fsdp', None), o_weight_nhd=('tp', None, 'fsdp'), ffw_weight_df=('fsdp', 'tp'), ffw_weight_fd=('tp', 'fsdp'), rms_norm_weight=('tp',), act_btd=('fsdp', None, 'tp'), act_btf=('fsdp', None, 'tp'), act_btnh=('fsdp', None, 'tp', None)), remat_config=<RematConfig.NONE: 1>, param_dtype=<class 'jax.num

Base Gemma3 model loaded ✅


LoRA policy model created ✅
Final EOS_TOKENS used for sampling: [1, 106]
